# Capstone Project - The Battle of the Neighborhoods
### Applied Data Science Capstone by IBM/Coursera
### By: Matias Garib

This Jupyter Notebook contains all the code and brief comments of the Coursera Capstone project. The full report will be accessible in the following Github Repository: https://github.com/MatiasGarib/Coursera_Capstone

## Table of contents
* [Introduction: Business Problem]
* [Importing Datasets]
* [Data Cleaning]
* [Methodology]
* [Analysis]
* [Results and Discussion]
* [Conclusion]

--------------------
<h2> Introduction <h2>


People want to start going out and visiting restaurants, but they want to visit places with the best hygiene practices. The questions we want to answer, for the city of San Francisco, are: which are the cleanest restaurants in each neighborhood? Which are the safest neighborhoods to go out to eat?

--------------------

-----------------------------
<h2> Importing Datasets <h2>

1. The first dataset to be used consists of a **GeoJSON file with the names and boundaries of 92 San Francisco neighborhoods (GeoJSON)** 
2. **Foursquare APIs (URI)**
3. City of San Francisco Health Department’s **hygiene inspection program (CSV)** 

-----------------------------


In [356]:
pip install sodapy

Note: you may need to restart the kernel to use updated packages.


In [317]:
pip install fuzzy_pandas

Note: you may need to restart the kernel to use updated packages.


In [1]:
#Import required libraries
import pandas as pd
import numpy as np
import requests
import folium
import fuzzy_pandas as fpd
from sodapy import Socrata



<h3>SF neighborhoods and Hygiene Data<h3>

The neighborhoods and hygiene inspection datasets are easily accessible thanks to the Socrata API provided by the San Francisco Government

In [52]:
#Import Hygiene and Nhoods dataframes
client = Socrata("data.sfgov.org", None)
results = client.get("pyih-qa8i", limit=60000)
hygiene_df=pd.DataFrame.from_records(results)

nhoods=client.get("743h-p4bq", limit=60000) # We will use this JSON file later on to map out San Francisco's neighborhoods
nhoods_df=pd.DataFrame.from_records(nhoods)

In [53]:
print(hygiene_df.shape)
print(nhoods_df.shape)

(53973, 23)
(92, 4)


In [54]:
nhoods_df.head(2)

sfar_distr  \
0  District 6 - Central North   
1  District 6 - Central North   

                                            the_geom       nbrhood nid  
0  {'type': 'MultiPolygon', 'coordinates': [[[[-1...  Alamo Square  6e  
1  {'type': 'MultiPolygon', 'coordinates': [[[[-1...    Anza Vista  6a

In [55]:
hygiene_df.head(2)

business_id            business_name  business_address  business_city  \
0       69618  Fancy Wheatfield Bakery  1362 Stockton St  San Francisco   
1       97975               BREADBELLY   1408 Clement St  San Francisco   

  business_state business_postal_code   inspection_id  \
0             CA                94133  69618_20190304   
1             CA                94118  97975_20190725   

           inspection_date        inspection_type           violation_id  ...  \
0  2019-03-04T00:00:00.000              Complaint  69618_20190304_103130  ...   
1  2019-07-25T00:00:00.000  Routine - Unscheduled  97975_20190725_103124  ...   

  inspection_score business_latitude business_longitude business_location  \
0              NaN               NaN                NaN               NaN   
1               96               NaN                NaN               NaN   

  :@computed_region_fyvs_ahh9 :@computed_region_p5aj_wyqh  \
0                         NaN                         NaN   
1                         NaN                         NaN   

  :@computed_region_rxqg_mtj9 :@computed_region_yftq_j783  \
0                         NaN                         NaN   
1                         NaN                         NaN   

  :@computed_region_bh8s_q3mv :@computed_region_ajp5_b2md  
0                         NaN                         NaN  
1                         NaN                         NaN  

[2 rows x 23 columns]

<h3> Foursquare <h3>

We will now use the Foursquare API to search each neighborhoods restaurants

In [56]:
#Setup my Foursquare account
client_id = 'U0BHFR2CGBOER0NS2E3LDULEVT032SXA3KVWLR2U1RTQBJCV' # your Foursquare ID
client_secret = 'WRRQIHUGH45BSIKD4HCNE5ZXRNAK3E1JJNIXVNRVBNYLZYEC' # your Foursquare Secret
version = '20180605' # Foursquare API version
category= '4d4b7105d754a06374d81259' #Food Category
limit=1000


print('Your credentails:')
print('CLIENT_ID: ' + client_id)
print('CLIENT_SECRET:' + client_secret)

Your credentails:
CLIENT_ID: U0BHFR2CGBOER0NS2E3LDULEVT032SXA3KVWLR2U1RTQBJCV
CLIENT_SECRET:WRRQIHUGH45BSIKD4HCNE5ZXRNAK3E1JJNIXVNRVBNYLZYEC


In [57]:
#I define a function that will get venues from all the Neighborhoods listed in our nhoods dataframe
def getVenuesLoc(names, radius=1000):
    
    venues_list=[]
    unexplored_nhoods=[]
    explored_nhoods=[]
    for name in names:
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&near={},San Francisco, CA&categoryId={}&radius={}&limit={}'.format(
        client_id,
        client_secret,
        version,
        name,
        category,
        radius, 
        limit)
            
        # make the GET request for neighbourhoods that don't throw error
        results = requests.get(url).json()
        if 'errorType' in results['meta']:
            print("Couldn't get venues from:", name)
            unexplored_nhoods.append(name)
        else:
            print(name)
            explored_nhoods.append(name)
            results = results["response"]['groups'][0]['items']
        # return only relevant information for each nearby venue
            venues_list.append([(
            name,
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
            nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
            nearby_venues.columns = ['Neighbourhood', 
                  'Venue', 
                  'Venue_Latitude', 
                  'Venue_Longitude', 
                  'Venue_Category']
    
    return(nearby_venues, explored_nhoods, unexplored_nhoods)

Becuase there are certain neighborhoods grouped, we ungroup them to apply the function

In [58]:
nhood_names=[]
for name in nhoods_df['nbrhood']:
    if '/' in name:
        split_name=name.split('/',1)
        nhood_names.append(split_name[0].strip())
        nhood_names.append(split_name[1].strip())
    elif '/' not in name:
        nhood_names.append(name)
    

In [59]:
sf_venues, explored_nhoods, unexplored_nhoods = getVenuesLoc(nhood_names)

Alamo Square
Anza Vista
Balboa Terrace
Couldn't get venues from: Bayview
Bernal Heights
Buena Vista Park
Ashbury Heights
Couldn't get venues from: Central Richmond
Central Sunset
Clarendon Heights
Couldn't get venues from: Corona Heights
Cow Hollow
Crocker Amazon
Couldn't get venues from: Diamond Heights
Downtown
Duboce Triangle
Couldn't get venues from: Eureka Valley
Couldn't get venues from: Dolores Heights
Excelsior
Financial District
Couldn't get venues from: Barbary Coast
Couldn't get venues from: Yerba Buena
Forest Hill
Couldn't get venues from: Forest Hills Extension
Forest Knolls
Glen Park
Golden Gate Heights
Golden Gate Park
Haight Ashbury
Hayes Valley
Hunters Point
Ingleside
Ingleside Heights
Ingleside Terrace
Couldn't get venues from: Inner Mission
Inner Parkside
Couldn't get venues from: Inner Richmond
Inner Sunset
Jordan Park
Laurel Heights
Couldn't get venues from: Lake Street
Monterey Heights
Couldn't get venues from: Lake Shore
Lakeside
Lone Mountain
Lower Pacific Heigh

In [60]:
print(sf_venues.shape)
print(hygiene_df.shape)
print(nhoods_df.shape)

(6120, 5)
(53973, 23)
(92, 4)


------------------------------------------
<h2> Data Cleaning  <h2>


By now we have thee data sets imported:
- SF Neighborhoods (92,4)
- Hygiene inspections (53973, 23)
- SF Venues from Foursquare API (5029)

Our approach will be the following:

1. Clean the Hygiene Inspections df by removing all inspections without a inspection score and removing duplicates (many restaurants are checked upon more than once, we will keep the latest inspection score)

2. Append the Hygien columns to our Venues df. Here we notice that names can vary a bit between df so we use *Fuzzy Merge* function to match similar but not exact strings.

------------------------------------------

In [61]:
hygiene_df.columns

Index(['business_id', 'business_name', 'business_address', 'business_city',
       'business_state', 'business_postal_code', 'inspection_id',
       'inspection_date', 'inspection_type', 'violation_id',
       'violation_description', 'risk_category', 'business_phone_number',
       'inspection_score', 'business_latitude', 'business_longitude',
       'business_location', ':@computed_region_fyvs_ahh9',
       ':@computed_region_p5aj_wyqh', ':@computed_region_rxqg_mtj9',
       ':@computed_region_yftq_j783', ':@computed_region_bh8s_q3mv',
       ':@computed_region_ajp5_b2md'],
      dtype='object')

In [62]:
#Removing Nan Values and keeping the important columns
hygiene_df=hygiene_df[['business_name','business_address','inspection_date', 'inspection_type','violation_description', 'risk_category','inspection_score' ]]
hygiene_df = hygiene_df[hygiene_df['inspection_score'].notna()]
hygiene_df

business_name  business_address          inspection_date  \
1                   BREADBELLY   1408 Clement St  2019-07-25T00:00:00.000   
2       Hakkasan San Francisco       1 Kearny St  2018-04-18T00:00:00.000   
4                      Tselogs      552 Jones St  2018-04-12T00:00:00.000   
8      The Estate Kitchen, LLC     799 Bryant St  2018-04-16T00:00:00.000   
9                 Beloved Cafe      3338 24th St  2018-05-02T00:00:00.000   
...                        ...               ...                      ...   
53967        El Gran Taco Loco  4591 Mission St.  2019-05-06T00:00:00.000   
53968       Blue Bottle Coffee      2 South Park  2019-05-06T00:00:00.000   
53970             Philz Coffee     300 Folsom St  2019-05-06T00:00:00.000   
53971        El Gran Taco Loco  4591 Mission St.  2019-05-06T00:00:00.000   
53972       Blue Bottle Coffee      2 South Park  2019-05-06T00:00:00.000   

             inspection_type  \
1      Routine - Unscheduled   
2      Routine - Unscheduled   
4      Routine - Unscheduled   
8      Routine - Unscheduled   
9      Routine - Unscheduled   
...                      ...   
53967  Routine - Unscheduled   
53968  Routine - Unscheduled   
53970  Routine - Unscheduled   
53971  Routine - Unscheduled   
53972  Routine - Unscheduled   

                                   violation_description  risk_category  \
1      Inadequately cleaned or sanitized food contact...  Moderate Risk   
2      Inadequate and inaccessible handwashing facili...  Moderate Risk   
4                               Improper thawing methods  Moderate Risk   
8                                  Improper food storage       Low Risk   
9                            Low risk vermin infestation       Low Risk   
...                                                  ...            ...   
53967            Insufficient hot water or running water  Moderate Risk   
53968  Inadequately cleaned or sanitized food contact...  Moderate Risk   
53970             Foods not protected from contamination  Moderate Risk   
53971  Inadequate food safety knowledge or lack of ce...  Moderate Risk   
53972  Food safety certificate or food handler card n...       Low Risk   

      inspection_score  
1                   96  
2                   88  
4                   94  
8                   86  
9                   96  
...                ...  
53967               76  
53968               80  
53970               92  
53971               76  
53972               80  

[39541 rows x 7 columns]

In [63]:
#Removing duplicates from the hygiene df
hygiene_df=hygiene_df.sort_values('inspection_date', ascending=False).drop_duplicates(subset='business_name', keep='first')
hygiene_df

business_name        business_address  \
14552                 Frisco Fried            5176 03rd St   
6787                 Cafe Majestic          1500 SUTTER St   
13344              Sears Fine Food           439 Powell St   
11908                Tokyo Express   160 Spear St Lobby ID   
14354   SHERIDAN ELEMENTARY SCHOOL         431 CAPITOL Ave   
...                            ...                     ...   
25331  Sally's Restaurant and Deli     300 De Haro St #332   
27998                  CATER THYME    1 UNITED NATIONS Plz   
24684            Way To Life Foods  1 United Nations Plaza   
24270              Hey Hey Gourmet  1 United Nations Plaza   
22715          Christine's Sausage  1 United Nations Plaza   

               inspection_date        inspection_type  \
14552  2019-10-03T00:00:00.000  Routine - Unscheduled   
6787   2019-10-03T00:00:00.000  Routine - Unscheduled   
13344  2019-10-03T00:00:00.000  Routine - Unscheduled   
11908  2019-10-03T00:00:00.000  Routine - Unscheduled   
14354  2019-10-03T00:00:00.000  Routine - Unscheduled   
...                        ...                    ...   
25331  2016-10-06T00:00:00.000  Routine - Unscheduled   
27998  2016-10-05T00:00:00.000  Routine - Unscheduled   
24684  2016-10-05T00:00:00.000  Routine - Unscheduled   
24270  2016-10-05T00:00:00.000  Routine - Unscheduled   
22715  2016-10-05T00:00:00.000  Routine - Unscheduled   

                                   violation_description  risk_category  \
14552                        Low risk vermin infestation       Low Risk   
6787                         Low risk vermin infestation       Low Risk   
13344   Unapproved or unmaintained equipment or utensils       Low Risk   
11908             Foods not protected from contamination  Moderate Risk   
14354  Inadequate food safety knowledge or lack of ce...  Moderate Risk   
...                                                  ...            ...   
25331       Unclean or degraded floors walls or ceilings       Low Risk   
27998                                                NaN            NaN   
24684                                                NaN            NaN   
24270                                                NaN            NaN   
22715                                                NaN            NaN   

      inspection_score  
14552               92  
6787                84  
13344               91  
11908               87  
14354               92  
...                ...  
25331               71  
27998              100  
24684              100  
24270              100  
22715              100  

[5277 rows x 7 columns]

In [64]:
#Fuzzy Merge between the two datasets
sf_venues=fpd.fuzzy_merge(sf_venues, hygiene_df,
                        keep='all',
                        left_on=['Venue'],
                        right_on=['business_name'],
                        method='metaphone',
                        ignore_nonalpha=True,
                        ignore_nonlatin=True,
                        ignore_case=True,
                        join='inner')

sf_venues.head()

Neighbourhood                  Venue  Venue_Latitude  Venue_Longitude  \
0  Alamo Square      Little Star Pizza       37.777489      -122.438281   
1  Alamo Square  Brenda's Meat & Three       37.778265      -122.438584   
2  Alamo Square               The Mill       37.776425      -122.437970   
3  Alamo Square        Jane the Bakery       37.783797      -122.434283   
4  Alamo Square           The Progress       37.783745      -122.432972   

                    Venue_Category         business_name   business_address  \
0                      Pizza Place     Little Star Pizza     846 Divisadero   
1  Southern / Soul Food Restaurant  Brendas Meat & Three  919 DIVISADERO ST   
2                           Bakery              The Mill  736 DIVISADERO St   
3                           Bakery       Jane the Bakery    1875 Geary Blvd   
4              American Restaurant          The Progress   1525 Fillmore St   

           inspection_date        inspection_type  \
0  2018-04-24T00:00:00.000  Routine - Unscheduled   
1  2019-03-13T00:00:00.000  Routine - Unscheduled   
2  2019-04-11T00:00:00.000  Routine - Unscheduled   
3  2019-07-03T00:00:00.000  Routine - Unscheduled   
4  2019-02-14T00:00:00.000  Routine - Unscheduled   

                              violation_description  risk_category  \
0                                               NaN            NaN   
1  Unapproved or unmaintained equipment or utensils       Low Risk   
2  Unapproved or unmaintained equipment or utensils       Low Risk   
3       Unclean or unsanitary food contact surfaces      High Risk   
4            Moderate risk food holding temperature  Moderate Risk   

  inspection_score  
0              100  
1               92  
2               88  
3               87  
4               90

In [65]:
sf_venues.shape

(5223, 12)

In [70]:
print(sf_venues['risk_category'].isna().sum())
print(sf_venues['violation_description'].isna().sum())
print((sf_venues['inspection_score']==100).sum())

312
312
286


In [68]:
# We notice how columns with no violation description and no risk category assigned are the ones with inspection score 100
sf_venues['inspection_score'] = sf_venues['inspection_score'].astype(int)
sf_venues[(sf_venues['violation_description'].isna()) & (sf_venues['risk_category'].isna()) & (sf_venues['inspection_score']==100)]

Neighbourhood                    Venue  Venue_Latitude  Venue_Longitude  \
0     Alamo Square        Little Star Pizza       37.777489      -122.438281   
22    Alamo Square  Lady Falcon Coffee Club       37.775969      -122.433959   
26    Alamo Square                  Zaytoon       37.775185      -122.437896   
39    Alamo Square                Gardenias       37.786109      -122.432710   
83      Anza Vista        Little Star Pizza       37.777489      -122.438281   
...            ...                      ...             ...              ...   
5165      Nob Hill               Acquerello       37.791669      -122.421407   
5171      Nob Hill                     1760       37.793206      -122.421211   
5175      Nob Hill             Another Cafe       37.790169      -122.415404   
5195      Nob Hill                Rue Lepic       37.790913      -122.410770   
5200      Nob Hill             The Saratoga       37.787097      -122.418201   

                Venue_Category            business_name  \
0                  Pizza Place        Little Star Pizza   
22                  Food Truck  Lady Falcon Coffee Club   
26    Mediterranean Restaurant                 ST. ANNE   
39                  Restaurant             Gratta Wines   
83                 Pizza Place        Little Star Pizza   
...                        ...                      ...   
5165        Italian Restaurant               Acquerello   
5171   New American Restaurant                      903   
5175                      Café             Another Cafe   
5195         French Restaurant                Rue Lepic   
5200       American Restaurant             The Saratoga   

                           business_address          inspection_date  \
0                            846 Divisadero  2018-04-24T00:00:00.000   
22    Beach Chalet Soccer Field Parking Lot  2017-04-15T00:00:00.000   
26                            1320 14th Ave  2018-11-30T00:00:00.000   
39                           5273 B 03rd St  2019-05-20T00:00:00.000   
83                           846 Divisadero  2018-04-24T00:00:00.000   
...                                     ...                      ...   
5165                     1722 Sacramento St  2018-11-07T00:00:00.000   
5171                       1566 Carroll Ave  2019-04-18T00:00:00.000   
5175                           1191 Pine St  2019-06-17T00:00:00.000   
5195                            900 Pine St  2019-06-03T00:00:00.000   
5200                         1000 Larkin St  2019-08-22T00:00:00.000   

            inspection_type violation_description risk_category  \
0     Routine - Unscheduled                   NaN           NaN   
22    Routine - Unscheduled                   NaN           NaN   
26    Routine - Unscheduled                   NaN           NaN   
39    Routine - Unscheduled                   NaN           NaN   
83    Routine - Unscheduled                   NaN           NaN   
...                     ...                   ...           ...   
5165  Routine - Unscheduled                   NaN           NaN   
5171  Routine - Unscheduled                   NaN           NaN   
5175  Routine - Unscheduled                   NaN           NaN   
5195  Routine - Unscheduled                   NaN           NaN   
5200  Routine - Unscheduled                   NaN           NaN   

      inspection_score  
0                  100  
22                 100  
26                 100  
39                 100  
83                 100  
...                ...  
5165               100  
5171               100  
5175               100  
5195               100  
5200               100  

[285 rows x 12 columns]

In [81]:
#So we change them to No Risk and No Violation
sf_venues['violation_description'] = np.where((sf_venues['inspection_score']==100) , 'No Violation', sf_venues['violation_description'])
sf_venues['risk_category'] = np.where((sf_venues['inspection_score']==100) , 'No risk', sf_venues['risk_category'])
sf_venues

Neighbourhood                     Venue  Venue_Latitude  Venue_Longitude  \
0     Alamo Square         Little Star Pizza       37.777489      -122.438281   
1     Alamo Square     Brenda's Meat & Three       37.778265      -122.438584   
2     Alamo Square                  The Mill       37.776425      -122.437970   
3     Alamo Square           Jane the Bakery       37.783797      -122.434283   
4     Alamo Square              The Progress       37.783745      -122.432972   
...            ...                       ...             ...              ...   
5218      Nob Hill           Osso Steakhouse       37.791447      -122.413530   
5219      Nob Hill             Batter Bakery       37.789551      -122.420776   
5220      Nob Hill  Nobhill Pizza & Shawerma       37.790767      -122.419747   
5221      Nob Hill        Kasa Indian Eatery       37.789655      -122.420449   
5222      Nob Hill   Golden Horse Restaurant       37.790860      -122.417340   

                       Venue_Category             business_name  \
0                         Pizza Place         Little Star Pizza   
1     Southern / Soul Food Restaurant      Brendas Meat & Three   
2                              Bakery                  The Mill   
3                              Bakery           Jane the Bakery   
4                 American Restaurant              The Progress   
...                               ...                       ...   
5218                       Steakhouse           Osso Steakhouse   
5219                           Bakery             Batter Bakery   
5220                      Pizza Place  Nobhill Pizza & Shawerma   
5221                Indian Restaurant        Kasa Indian Eatery   
5222               Chinese Restaurant   Golden Horse Restaurant   

        business_address          inspection_date        inspection_type  \
0         846 Divisadero  2018-04-24T00:00:00.000  Routine - Unscheduled   
1      919 DIVISADERO ST  2019-03-13T00:00:00.000  Routine - Unscheduled   
2      736 DIVISADERO St  2019-04-11T00:00:00.000  Routine - Unscheduled   
3        1875 Geary Blvd  2019-07-03T00:00:00.000  Routine - Unscheduled   
4       1525 Fillmore St  2019-02-14T00:00:00.000  Routine - Unscheduled   
...                  ...                      ...                    ...   
5218  1177 California St  2019-06-03T00:00:00.000  Routine - Unscheduled   
5219        1517 Pine St  2018-08-21T00:00:00.000  Routine - Unscheduled   
5220  1534 California St  2019-09-23T00:00:00.000  Routine - Unscheduled   
5221        4001 18th St  2019-09-23T00:00:00.000  Routine - Unscheduled   
5222        1060 Hyde St  2018-01-23T00:00:00.000  Routine - Unscheduled   

                                  violation_description  risk_category  \
0                                          No Violation        No risk   
1      Unapproved or unmaintained equipment or utensils       Low Risk   
2      Unapproved or unmaintained equipment or utensils       Low Risk   
3           Unclean or unsanitary food contact surfaces      High Risk   
4                Moderate risk food holding temperature  Moderate Risk   
...                                                 ...            ...   
5218  Inadequately cleaned or sanitized food contact...  Moderate Risk   
5219  Wiping cloths not clean or properly stored or ...       Low Risk   
5220                 High risk food holding temperature      High Risk   
5221            Insufficient hot water or running water  Moderate Risk   
5222             Foods not protected from contamination  Moderate Risk   

      inspection_score  
0                  100  
1                   92  
2                   88  
3                   87  
4                   90  
...                ...  
5218                96  
5219                98  
5220                93  
5221                86  
5222                79  

[5223 rows x 12 columns]

In [91]:
# We finally drop the remainding Nan values to get our final df
sf_venues = sf_venues[sf_venues['violation_description'].notna()]
sf_venues = sf_venues[sf_venues['risk_category'].notna()]
sf_venues

Neighbourhood                     Venue  Venue_Latitude  Venue_Longitude  \
0     Alamo Square         Little Star Pizza       37.777489      -122.438281   
1     Alamo Square     Brenda's Meat & Three       37.778265      -122.438584   
2     Alamo Square                  The Mill       37.776425      -122.437970   
3     Alamo Square           Jane the Bakery       37.783797      -122.434283   
4     Alamo Square              The Progress       37.783745      -122.432972   
...            ...                       ...             ...              ...   
5218      Nob Hill           Osso Steakhouse       37.791447      -122.413530   
5219      Nob Hill             Batter Bakery       37.789551      -122.420776   
5220      Nob Hill  Nobhill Pizza & Shawerma       37.790767      -122.419747   
5221      Nob Hill        Kasa Indian Eatery       37.789655      -122.420449   
5222      Nob Hill   Golden Horse Restaurant       37.790860      -122.417340   

                       Venue_Category             business_name  \
0                         Pizza Place         Little Star Pizza   
1     Southern / Soul Food Restaurant      Brendas Meat & Three   
2                              Bakery                  The Mill   
3                              Bakery           Jane the Bakery   
4                 American Restaurant              The Progress   
...                               ...                       ...   
5218                       Steakhouse           Osso Steakhouse   
5219                           Bakery             Batter Bakery   
5220                      Pizza Place  Nobhill Pizza & Shawerma   
5221                Indian Restaurant        Kasa Indian Eatery   
5222               Chinese Restaurant   Golden Horse Restaurant   

        business_address          inspection_date        inspection_type  \
0         846 Divisadero  2018-04-24T00:00:00.000  Routine - Unscheduled   
1      919 DIVISADERO ST  2019-03-13T00:00:00.000  Routine - Unscheduled   
2      736 DIVISADERO St  2019-04-11T00:00:00.000  Routine - Unscheduled   
3        1875 Geary Blvd  2019-07-03T00:00:00.000  Routine - Unscheduled   
4       1525 Fillmore St  2019-02-14T00:00:00.000  Routine - Unscheduled   
...                  ...                      ...                    ...   
5218  1177 California St  2019-06-03T00:00:00.000  Routine - Unscheduled   
5219        1517 Pine St  2018-08-21T00:00:00.000  Routine - Unscheduled   
5220  1534 California St  2019-09-23T00:00:00.000  Routine - Unscheduled   
5221        4001 18th St  2019-09-23T00:00:00.000  Routine - Unscheduled   
5222        1060 Hyde St  2018-01-23T00:00:00.000  Routine - Unscheduled   

                                  violation_description  risk_category  \
0                                          No Violation        No risk   
1      Unapproved or unmaintained equipment or utensils       Low Risk   
2      Unapproved or unmaintained equipment or utensils       Low Risk   
3           Unclean or unsanitary food contact surfaces      High Risk   
4                Moderate risk food holding temperature  Moderate Risk   
...                                                 ...            ...   
5218  Inadequately cleaned or sanitized food contact...  Moderate Risk   
5219  Wiping cloths not clean or properly stored or ...       Low Risk   
5220                 High risk food holding temperature      High Risk   
5221            Insufficient hot water or running water  Moderate Risk   
5222             Foods not protected from contamination  Moderate Risk   

      inspection_score  
0                  100  
1                   92  
2                   88  
3                   87  
4                   90  
...                ...  
5218                96  
5219                98  
5220                93  
5221                86  
5222                79  

[5196 rows x 12 columns]

NICE! We have 5196 restaurants in our DF, all of which contain location information (neighborhood, lat , long) as well as hygiene data. We can map them out to finish this section

In [92]:
sf_center = [37.7749, -122.4194]
sf_map = folium.Map(location=sf_center, zoom_start=13)
folium.Marker(sf_center, popup='City Center').add_to(sf_map)
for name, lat, lng in zip(sf_venues.Venue, sf_venues.Venue_Latitude, sf_venues.Venue_Longitude):
    color = 'blue'
    folium.CircleMarker([lat, lng], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(sf_map)
sf_map

------------------------------------------
<h2> Methodology  <h2>

This project's main goal is to classify each of San Francisco's neghborhoods according to their restaurants infection risk.

(1) We've already imported and cleaned the datasets and now have a large datasets of restaurants and their hygiene inspection results

(2) We'll first perform a visual inspection of the data, visualizing for all of San Francisco which are high restaurant density spots. We will also create cloropleth maps with the inspection score points per neighborhood.

(3) The final analysis will focus on the neighborhood divisions. We will create indicators of risk density to cluster neighborhoods according to their restaurants hygiene practices and denisty. The best neighborhoods to go out to dinner will be the ones where there are most restaurants and where these have high hygiene standards. 


------------------------------------------

<h3> Visual Inspection: Restaurant Heatmaps  <h3>

In [130]:
#We first pre process the data for inspection
restaurants_latlng=sf_venues[['Venue_Latitude','Venue_Longitude']]
restaurants_latlng['Venue_Latitude']=restaurants_latlng['Venue_Latitude'].astype(float)
restaurants_latlng['Venue_Longitude']=restaurants_latlng['Venue_Longitude'].astype(float)
restaurants_latlng_list=restaurants_latlng.values.tolist()

In [135]:
from folium import plugins
from folium.plugins import HeatMap


sf_map = folium.Map(location=sf_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(sf_map)
HeatMap(restaurants_latlng_list).add_to(sf_map)
folium.Marker(sf_center).add_to(sf_map)
folium.GeoJson(nhoods, name='json').add_to(sf_map)
sf_map

ValueError: Unhandled object [{'sfar_distr': 'District 6 - Central North', 'the_geom': {'type': 'MultiPolygon', 'coordinates': [[[[-122.42948394891741, 37.775096230704314], [-122.43101153840207, 37.77490283132814], [-122.43264862289246, 37.77469266061221], [-122.43429428444675, 37.77447581662921], [-122.43594032806337, 37.77427667844604], [-122.4376106240872, 37.774061646405066], [-122.43774490824637, 37.774044328330085], [-122.43867122231956, 37.77861526930866], [-122.43345910855257, 37.77927771863689], [-122.4331005636341, 37.77750542996215], [-122.43157464229915, 37.77769992520567], [-122.43005093549058, 37.77789364870233], [-122.43003059443478, 37.77780251540478], [-122.43003083164434, 37.77780248523876], [-122.42987991643541, 37.77705573292902], [-122.42948394891741, 37.775096230704314]]]]}, 'nbrhood': 'Alamo Square', 'nid': '6e'}, {'sfar_distr': 'District 6 - Central North', 'the_geom': {'type': 'MultiPolygon', 'coordinates': [[[[-122.44746439135872, 37.77986335309237], [-122.447